In [1]:
# initial imports
import pandas as pd
from path import Path

from sklearn.cluster import KMeans
import plotly.express as px
import hvplot.pandas
import numpy as np
from sklearn.preprocessing import StandardScaler
data_scaler = StandardScaler()

### Divide the stock data in two parts. From 4/28/2020 - 1/21/2021 (before) and 2/04/2021 - 10/28/2021 (after). 
#### Note we are not counting 9 nine days of data when the GME explosion happened. 

In [2]:
# Import and prepare GameStop (GME) stock data
file_path1 = Path("Resources/GME.csv")
GME_df = pd.read_csv(file_path1)
print(GME_df.shape)
GME_df.head(5)

(461, 7)


Date  Open  High   Low  Close  Adj Close   Volume
0  2020-01-02  6.14  6.47  6.07   6.31       6.31  4453600
1  2020-01-03  6.21  6.25  5.84   5.88       5.88  3543900
2  2020-01-06  5.80  5.91  5.60   5.85       5.85  3394800
3  2020-01-07  5.77  5.83  5.44   5.52       5.52  5228000
4  2020-01-08  5.49  5.85  5.41   5.72       5.72  5629400

In [3]:
# GME_stock_df = mstock_df[mstock_df[("Ticker")] == "GME"]
GME_copy = GME_df.copy()

# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
GME_copy["b_ref_Close"] = GME_copy["Adj Close"] - 5.64

# Calculate the % change from the reference day
GME_copy["b_Perc_ref"] = (GME_copy["Adj Close"] - 5.64)/5.64

# Use a new ref_Close price ($53.5), Feb 04, 2021 (after the GME craziness)
GME_copy["a_ref_Close"] = GME_copy["Adj Close"] - 53.5
# New % change from the new reference day: Feb 04, 2021
GME_copy["a_Perc_ref"] = (GME_copy["Adj Close"] - 53.5)/53.5

print(GME_copy.shape)
GME_copy.tail()

(461, 11)


Date        Open        High         Low       Close   Adj Close  \
456  2021-10-22  178.100006  179.490005  167.800003  169.800003  169.800003   
457  2021-10-25  169.419998  174.800003  167.259995  173.970001  173.970001   
458  2021-10-26  173.360001  185.000000  172.500000  177.839996  177.839996   
459  2021-10-27  180.000000  183.089996  172.330002  173.509995  173.509995   
460  2021-10-28  175.160004  183.139999  175.000000  182.850006  182.850006   

      Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
456  2800400   164.160003   29.106384   116.300003    2.173832  
457  1442800   168.330001   29.845745   120.470001    2.251776  
458  2176700   172.199996   30.531914   124.339996    2.324112  
459  1107000   167.869995   29.764184   120.009995    2.243177  
460  1696200   177.210006   31.420214   129.350006    2.417757

#### Import and prepare AMC stocks

In [4]:
# Import AMC stocks
file_path2 = Path("Resources/AMC.csv")
AMC_df = pd.read_csv(file_path2)
# Drop the "Close" price and keep "Adj Close" price
# AMC_clean_df = AMC_df.drop(columns = "Close")
print(AMC_df.shape)
AMC_df.head(5)

(462, 7)


Date  Open  High   Low  Close  Adj Close   Volume
0  2020-01-02  7.30  7.56  7.23   7.46   7.414512  4545900
1  2020-01-03  7.45  7.60  7.31   7.32   7.275366  2218000
2  2020-01-06  7.25  7.30  7.11   7.12   7.076585  2903400
3  2020-01-07  7.11  7.20  7.00   7.13   7.086524  3205300
4  2020-01-08  7.11  7.15  6.61   6.62   6.579634  6557000

In [5]:
AMC_copy = AMC_df.copy()
# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
AMC_copy["b_ref_Close"] = AMC_copy["Adj Close"] - 4.14

# Calculate the % change from the reference day
AMC_copy["b_Perc_ref"] = (AMC_copy["Adj Close"] - 4.14)/4.14

# Use a new ref_Close price ($7.09), Feb 04, 2021 (after the GME craziness)
AMC_copy["a_ref_Close"] = AMC_copy["Adj Close"] - 7.09
# New % change from the new reference day: Feb 04, 2021
AMC_copy["a_Perc_ref"] = (AMC_copy["Adj Close"] - 7.09)/7.09
 
print(AMC_copy.shape)
AMC_copy.tail()

(462, 11)


Date       Open       High        Low      Close  Adj Close  \
457  2021-10-25  36.230000  37.849998  35.779999  36.830002  36.830002   
458  2021-10-26  36.529999  37.400002  35.779999  36.049999  36.049999   
459  2021-10-27  36.330002  36.790001  34.580002  34.759998  34.759998   
460  2021-10-28  35.090000  36.070000  34.860001  35.230000  35.230000   
461  2021-10-29  35.340000  36.630001  34.529999  35.369999  35.369999   

       Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
457  30905400    32.690002    7.896136    29.740002    4.194641  
458  27674800    31.909999    7.707729    28.959999    4.084626  
459  25904100    30.619998    7.396135    27.669998    3.902680  
460  23812200    31.090000    7.509662    28.140000    3.968970  
461  32841500    31.229999    7.543478    28.279999    3.988716

#### Import and prepare BBBY stocks

In [6]:
# Import Bed Batch and Beyond (BBBY) stocks
file_path3 = Path("Resources/BBBY.csv")
BBBY_df = pd.read_csv(file_path3)
# # Drop the "Close" price and keep "Adj Close" price
# BBBY_clean_df = BBBY_df.drop(columns = "Close")
print(BBBY_df.shape)
BBBY_df.head(5)

(462, 7)


Date   Open       High        Low      Close  Adj Close    Volume
0  2020-01-02  17.43  17.440001  16.160000  16.330000  15.967111   6695000
1  2020-01-03  16.08  16.370001  15.860000  16.080000  15.722667   4116400
2  2020-01-06  16.48  16.930000  16.200001  16.559999  16.191999   8120600
3  2020-01-07  16.60  16.930000  16.110001  16.840000  16.465778   7960500
4  2020-01-08  16.74  17.110001  16.540001  16.650000  16.279999  13688800

In [7]:
# Shift the reference point to the start date
BBBY_copy = BBBY_df.copy()

# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
BBBY_copy["b_ref_Close"] = BBBY_copy["Adj Close"] - 6.65
# Calculate the % change from the reference day
BBBY_copy["b_Perc_ref"] = (BBBY_copy["Adj Close"] - 6.65)/6.65

# Use a new ref_Close price ($27.01), Feb 02, 2021 (after the GME craziness)
BBBY_copy["a_ref_Close"] = BBBY_copy["Adj Close"] - 27.01
# New % change from the new reference day: Feb 04, 2021
BBBY_copy["a_Perc_ref"] = (BBBY_copy["Adj Close"] - 27.01)/27.01

print(BBBY_copy.shape)
BBBY_copy.tail()

(462, 11)


Date   Open   High    Low  Close  Adj Close   Volume  b_ref_Close  \
457  2021-10-25  14.24  14.80  14.04  14.46      14.46  3390500         7.81   
458  2021-10-26  14.45  14.66  14.01  14.13      14.13  4089200         7.48   
459  2021-10-27  14.11  14.13  13.38  13.67      13.67  8415400         7.02   
460  2021-10-28  13.85  14.41  13.55  14.39      14.39  7038200         7.74   
461  2021-10-29  14.45  14.73  13.98  14.04      14.04  5368700         7.39   

     b_Perc_ref  a_ref_Close  a_Perc_ref  
457    1.174436       -12.55   -0.464643  
458    1.124812       -12.88   -0.476860  
459    1.055639       -13.34   -0.493891  
460    1.163910       -12.62   -0.467234  
461    1.111278       -12.97   -0.480193

#### Import and prepare VOO (Vanguard S&P 500 ETF)

In [8]:
# Import Vanguard S&P 500 ETF (VOO) index fund
file_path4 = Path("Resources/VOO.csv")
VOO_df = pd.read_csv(file_path4)
# # Drop the "Close" price and keep "Adj Close" price
# VOO_clean_df = VOO_df.drop(columns = "Close")
print(VOO_df.shape)
VOO_df.head(5)

(462, 7)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  297.290009  298.450012  296.339996  298.420013  290.068878   
1  2020-01-03  295.220001  297.359985  295.040009  296.239990  287.949829   
2  2020-01-06  294.420013  297.420013  294.350006  297.350006  289.028778   
3  2020-01-07  296.820007  297.269989  296.059998  296.529999  288.231720   
4  2020-01-08  296.709991  299.309998  296.470001  298.059998  289.718933   

    Volume  
0  3142400  
1  3247900  
2  2777100  
3  2251800  
4  3719500

In [9]:
# Shift the reference point to the start date
VOO_copy = VOO_df.copy()

# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
VOO_copy["b_ref_Close"] = VOO_copy["Adj Close"] - 256.527618
# Calculate the % change from the reference day
VOO_copy["b_Perc_ref"] = (VOO_copy["Adj Close"] - 256.527618)/256.527618

# Use a new ref_Close price ($351.424042), Feb 04, 2021 (after the GME craziness)
VOO_copy["a_ref_Close"] = VOO_copy["Adj Close"] - 351.424042
# New % change from the new reference day: Feb 04, 2021
VOO_copy["a_Perc_ref"] = (VOO_copy["Adj Close"] - 351.424042)/351.424042

print(VOO_copy.shape)
VOO_copy.tail()

(462, 11)


Date        Open        High         Low       Close   Adj Close  \
457  2021-10-25  417.640015  419.140015  415.929993  418.750000  418.750000   
458  2021-10-26  420.269989  421.529999  418.859985  419.149994  419.149994   
459  2021-10-27  419.660004  420.290009  417.279999  417.329987  417.329987   
460  2021-10-28  418.779999  421.440002  418.750000  421.410004  421.410004   
461  2021-10-29  419.149994  422.519989  418.869995  422.160004  422.160004   

      Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
457  2511500   162.222382    0.632378    67.325958    0.191580  
458  3085300   162.622376    0.633937    67.725952    0.192719  
459  2873500   160.802369    0.626842    65.905945    0.187540  
460  3643600   164.882386    0.642747    69.985962    0.199150  
461  4637400   165.632386    0.645671    70.735962    0.201284

In [10]:
# Import and prepare Biontech (BNTX) stocks
file_path5 = Path("Resources/BNTX.csv")
BNTX_df = pd.read_csv(file_path5)
print(BNTX_df.shape)
BNTX_df.head(5)

(462, 7)


Date       Open       High        Low      Close  Adj Close  Volume
0  2020-01-02  35.750000  38.500000  35.360001  38.500000  38.500000  139500
1  2020-01-03  38.000000  41.250000  36.419998  40.049999  40.049999  176000
2  2020-01-06  40.110001  45.000000  40.099998  44.580002  44.580002  333300
3  2020-01-07  47.400002  48.849998  41.180000  43.340000  43.340000  562100
4  2020-01-08  44.299999  46.330002  44.180000  45.099998  45.099998  193900

In [11]:
# Shift the reference point to the start date
BNTX_copy = BNTX_df.copy()

# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
BNTX_copy["b_ref_Close"] = BNTX_copy["Adj Close"] - 45.830002
# Calculate the % change from the reference day
BNTX_copy["b_Perc_ref"] = (BNTX_copy["Adj Close"] - 45.830002)/45.830002

# Use a new ref_Close price ($117.559998), Feb 04, 2021 (after the GME craziness)
BNTX_copy["a_ref_Close"] = BNTX_copy["Adj Close"] - 117.559998
# New % change from the new reference day: Feb 04, 2021
BNTX_copy["a_Perc_ref"] = (BNTX_copy["Adj Close"] - 117.559998)/117.559998

print(BNTX_copy.shape)
BNTX_copy.tail()

(462, 11)


Date        Open        High         Low       Close   Adj Close  \
457  2021-10-25  278.677002  295.510010  278.677002  294.920013  294.920013   
458  2021-10-26  295.510010  304.350006  290.630005  292.390015  292.390015   
459  2021-10-27  294.540009  297.950012  277.839996  278.769989  278.769989   
460  2021-10-28  282.500000  288.709991  277.100006  283.980011  283.980011   
461  2021-10-29  283.750000  284.850006  273.000000  278.730011  278.730011   

      Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
457  2853000   249.090011    5.435086   177.360015    1.508677  
458  2272400   246.560013    5.379882   174.830017    1.487156  
459  1914300   232.939987    5.082696   161.209991    1.371300  
460  1468500   238.150009    5.196378   166.420013    1.415618  
461  1462600   232.900009    5.081824   161.170013    1.370960

In [12]:
# Import and prepare American Express (AXP) stocks
file_path6 = Path("Resources/AXP.csv")
AXP_df = pd.read_csv(file_path6)
print(AXP_df.shape)
AXP_df.head(5)

(462, 7)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  124.660004  126.269997  124.230003  125.849998  122.641548   
1  2020-01-03  124.320000  125.099998  123.940002  124.599998  121.423416   
2  2020-01-06  123.370003  124.160004  123.120003  124.059998  120.897179   
3  2020-01-07  123.470001  124.400002  123.360001  123.410004  120.263756   
4  2020-01-08  124.050003  126.360001  123.800003  125.540001  122.339447   

    Volume  
0  2708000  
1  2090600  
2  2855200  
3  2042300  
4  3458200

In [13]:
# Shift the reference point to the start date, Jan 1, 2020
AXP_copy = AXP_df.copy()

# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
AXP_copy["b_ref_Close"] = AXP_copy["Adj Close"] - 86.41906
# Calculate the % change from the reference day
AXP_copy["b_Perc_ref"] = (AXP_copy["Adj Close"] - 86.41906)/86.41906

# Use a new ref_Close price ($123.893639), Feb 04, 2021 (after the GME craziness)
AXP_copy["a_ref_Close"] = AXP_copy["Adj Close"] - 123.893639
# New % change from the new reference day: Feb 04, 2021
AXP_copy["a_Perc_ref"] = (AXP_copy["Adj Close"] - 123.893639)/123.893639

print(AXP_copy.shape)
AXP_copy.head()

(462, 11)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  124.660004  126.269997  124.230003  125.849998  122.641548   
1  2020-01-03  124.320000  125.099998  123.940002  124.599998  121.423416   
2  2020-01-06  123.370003  124.160004  123.120003  124.059998  120.897179   
3  2020-01-07  123.470001  124.400002  123.360001  123.410004  120.263756   
4  2020-01-08  124.050003  126.360001  123.800003  125.540001  122.339447   

    Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
0  2708000    36.222488    0.419149    -1.252091   -0.010106  
1  2090600    35.004356    0.405054    -2.470223   -0.019938  
2  2855200    34.478119    0.398964    -2.996460   -0.024186  
3  2042300    33.844696    0.391635    -3.629883   -0.029298  
4  3458200    35.920387    0.415654    -1.554192   -0.012545

In [14]:
# Import and prepare Microsoft (MSFT) stocks
file_path7 = Path("Resources/MSFT.csv")
MSFT_df = pd.read_csv(file_path7)
print(MSFT_df.shape)
MSFT_df.head(5)

(462, 7)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  158.779999  160.729996  158.330002  160.619995  157.615128   
1  2020-01-03  158.320007  159.949997  158.059998  158.619995  155.652512   
2  2020-01-06  157.080002  159.100006  156.509995  159.029999  156.054855   
3  2020-01-07  159.320007  159.669998  157.320007  157.580002  154.631973   
4  2020-01-08  158.929993  160.800003  157.949997  160.089996  157.095032   

     Volume  
0  22622100  
1  21116200  
2  20813700  
3  21634100  
4  27746500

In [15]:
# Shift the reference point to the start date, Jan 1, 2020
MSFT_copy = MSFT_df.copy()

# Subtract the "Adj Close" price on April 28, 2020 price from future stocks.
# This is reference "zero"
MSFT_copy["b_ref_Close"] = MSFT_copy["Adj Close"] - 167.088333
# Calculate the % change from the reference day
MSFT_copy["b_Perc_ref"] = (MSFT_copy["Adj Close"] - 167.088333)/167.088333

# Use a new ref_Close price ($239.99826), Feb 02, 2021 (after the GME craziness)
MSFT_copy["a_ref_Close"] = MSFT_copy["Adj Close"] - 239.99826
# New % change from the new reference day: Feb 04, 2021
MSFT_copy["a_Perc_ref"] = (MSFT_copy["Adj Close"] - 239.99826)/239.99826

print(MSFT_copy.shape)
MSFT_copy.tail()

(462, 11)


Date        Open        High         Low       Close   Adj Close  \
457  2021-10-25  309.359985  309.399994  306.459991  308.130005  307.567322   
458  2021-10-26  311.000000  312.399994  308.600006  310.109985  309.543671   
459  2021-10-27  316.000000  326.100006  316.000000  323.170013  322.579865   
460  2021-10-28  324.329987  324.869995  321.359985  324.350006  323.757690   
461  2021-10-29  324.130005  332.000000  323.899994  331.619995  331.014404   

       Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
457  17554500   140.478989    0.840747    67.569062    0.281540  
458  28107300   142.455338    0.852575    69.545411    0.289775  
459  52588700   155.491532    0.930595    82.581605    0.344093  
460  26297900   156.669357    0.937644    83.759430    0.349000  
461  34744900   163.926071    0.981074    91.016144    0.379237

In [16]:
# Import and prepare DISNEY (DIS) stocks
file_path8 = Path("Resources/DIS.csv")
DIS_df = pd.read_csv(file_path8)
print(DIS_df.shape)
DIS_df.head(5)

(462, 7)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  145.289993  148.199997  145.100006  148.199997  148.199997   
1  2020-01-03  146.399994  147.899994  146.050003  146.500000  146.500000   
2  2020-01-06  145.539993  146.029999  144.309998  145.649994  145.649994   
3  2020-01-07  145.990005  146.869995  145.419998  145.699997  145.699997   
4  2020-01-08  145.490005  146.130005  144.820007  145.399994  145.399994   

    Volume  
0  9502100  
1  7320200  
2  8262500  
3  6906500  
4  6984200

In [17]:
# Shift the reference point to the start date, Jan 1, 2020
DIS_copy = DIS_df.copy()

# Subtract the "Adj Close" price on Apr 28, 2020 price from future stocks.
# This is reference "zero"
DIS_copy["b_ref_Close"] = DIS_copy["Adj Close"] - 106.209999
# Calculate the % change from the reference day
DIS_copy["b_Perc_ref"] = (DIS_copy["Adj Close"] - 106.209999)/106.209999

# Use a new ref_Close price ($180.229996), Feb 04, 2021 (after the GME craziness)
DIS_copy["a_ref_Close"] = DIS_copy["Adj Close"] - 180.229996
# New % change from the new reference day: Feb 04, 2021
DIS_copy["a_Perc_ref"] = (DIS_copy["Adj Close"] - 180.229996)/180.229996

print(DIS_copy.shape)
DIS_copy.head()

(462, 11)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  145.289993  148.199997  145.100006  148.199997  148.199997   
1  2020-01-03  146.399994  147.899994  146.050003  146.500000  146.500000   
2  2020-01-06  145.539993  146.029999  144.309998  145.649994  145.649994   
3  2020-01-07  145.990005  146.869995  145.419998  145.699997  145.699997   
4  2020-01-08  145.490005  146.130005  144.820007  145.399994  145.399994   

    Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
0  9502100    41.989998    0.395349   -32.029999   -0.177717  
1  7320200    40.290001    0.379343   -33.729996   -0.187150  
2  8262500    39.439995    0.371340   -34.580002   -0.191866  
3  6906500    39.489998    0.371811   -34.529999   -0.191589  
4  6984200    39.189995    0.368986   -34.830002   -0.193253

In [18]:
# Import and prepare Marathon Digital Holdings, Inc. (MARA) stocks
file_path9 = Path("Resources/MARA.csv")
MARA_df = pd.read_csv(file_path9)
print(MARA_df.shape)
MARA_df.head(5)

(462, 7)


Date  Open  High   Low  Close  Adj Close   Volume
0  2020-01-02  0.88  1.08  0.88   1.05       1.05   447600
1  2020-01-03  0.99  1.00  0.93   0.96       0.96   128000
2  2020-01-06  0.96  1.06  0.96   0.97       0.97   192100
3  2020-01-07  0.98  1.12  0.98   1.09       1.09  1039100
4  2020-01-08  1.13  1.13  0.92   0.95       0.95   487700

In [19]:
# Shift the reference point to the start date, Jan 1, 2020
MARA_copy = MARA_df.copy()

# Subtract the "Adj Close" price on Apr 28, 2020 price from future stocks.
# This is reference "zero"
MARA_copy["b_ref_Close"] = MARA_copy["Adj Close"] - 0.44
# Calculate the % change from the reference day
MARA_copy["b_Perc_ref"] = (MARA_copy["Adj Close"] - 0.44)/0.44

# Use a new ref_Close price ($22.799999), Feb 02, 2021 (after the GME craziness)
MARA_copy["a_ref_Close"] = MARA_copy["Adj Close"] - 22.799999
# New % change from the new reference day: Feb 04, 2021
MARA_copy["a_Perc_ref"] = (MARA_copy["Adj Close"] - 22.799999)/22.799999

print(MARA_copy.shape)
MARA_copy.tail()

(462, 11)


Date       Open       High        Low      Close  Adj Close  \
457  2021-10-25  51.099998  55.290001  51.009998  54.689999  54.689999   
458  2021-10-26  53.880001  54.959999  52.270000  52.860001  52.860001   
459  2021-10-27  50.820000  51.299999  48.900002  50.040001  50.040001   
460  2021-10-28  52.189999  53.680000  49.849998  50.389999  50.389999   
461  2021-10-29  50.830002  52.750000  49.799999  52.240002  52.240002   

       Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
457  14915800    54.249999  123.295452    31.890000    1.398684  
458  10082200    52.420001  119.136366    30.060002    1.318421  
459   8853300    49.600001  112.727275    27.240002    1.194737  
460  11053600    49.949999  113.522725    27.590000    1.210088  
461   9944600    51.800002  117.727277    29.440003    1.291228

In [20]:
# Import and prepare Electronic Arts, INC (EA) stocks
file_path10 = Path("Resources/EA.csv")
EA_df = pd.read_csv(file_path10)
print(EA_df.shape)
EA_df.head(5)

(462, 7)


Date        Open        High         Low       Close   Adj Close  \
0  2020-01-02  107.940002  108.349998  106.760002  107.339996  106.810196   
1  2020-01-03  105.580002  107.750000  105.120003  107.199997  106.670868   
2  2020-01-06  106.949997  109.309998  106.629997  108.779999  108.243073   
3  2020-01-07  109.000000  109.250000  107.730003  108.389999  107.855011   
4  2020-01-08  108.180000  110.000000  107.779999  109.489998  108.949577   

    Volume  
0  1901000  
1  1840300  
2  2934200  
3  1692400  
4  2651600

In [21]:
# Shift the reference point to the start date, Jan 1, 2020
EA_copy = EA_df.copy()

# Subtract the "Adj Close" price on Apr 28, 2020 price from future stocks.
# This is reference "zero"
EA_copy["b_ref_Close"] = EA_copy["Adj Close"] - 110.8004
# Calculate the % change from the reference day
EA_copy["b_Perc_ref"] = (EA_copy["Adj Close"] - 110.8004)/110.8004

# Use a new ref_Close price ($138.129562), Feb 02, 2021 (after the GME craziness)
EA_copy["a_ref_Close"] = EA_copy["Adj Close"] - 138.129562
# New % change from the new reference day: Feb 04, 2021
EA_copy["a_Perc_ref"] = (EA_copy["Adj Close"] - 138.129562)/138.129562

print(EA_copy.shape)
EA_copy.tail()

(462, 11)


Date        Open        High         Low       Close   Adj Close  \
457  2021-10-25  141.110001  143.789993  140.500000  142.190002  142.190002   
458  2021-10-26  142.919998  144.110001  141.720001  142.399994  142.399994   
459  2021-10-27  142.679993  142.759995  140.309998  140.369995  140.369995   
460  2021-10-28  140.250000  141.190002  139.100006  140.229996  140.229996   
461  2021-10-29  140.419998  140.839996  138.910004  140.250000  140.250000   

      Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
457  2155600    31.389602    0.283299     4.060440    0.029396  
458  1543000    31.599594    0.285194     4.270432    0.030916  
459  1697000    29.569595    0.266873     2.240433    0.016220  
460  1372600    29.429596    0.265609     2.100434    0.015206  
461  1990500    29.449600    0.265790     2.120438    0.015351

In [22]:
# Import and prepare Sony Group Corporation (SONY) stocks
file_path11 = Path("Resources/SONY.csv")
SONY_df = pd.read_csv(file_path11)
print(SONY_df.shape)
SONY_df.head(5)

(462, 7)


Date       Open       High        Low      Close  Adj Close   Volume
0  2020-01-02  68.300003  69.059998  68.279999  69.059998  69.059998   856500
1  2020-01-03  68.500000  68.650002  67.959999  68.080002  68.080002   518600
2  2020-01-06  68.250000  69.199997  68.220001  69.110001  69.110001   755500
3  2020-01-07  70.510002  70.580002  69.809998  70.199997  70.199997  1316200
4  2020-01-08  70.800003  71.120003  70.370003  70.459999  70.459999  1640200

In [23]:
# Shift the reference point to the start date, Jan 1, 2020
SONY_copy = SONY_df.copy()

# Subtract the "Adj Close" price on Apr 28, 2020 price from future stocks.
# This is reference "zero"
SONY_copy["b_ref_Close"] = SONY_copy["Adj Close"] - 62.919998
# Calculate the % change from the reference day
SONY_copy["b_Perc_ref"] = (SONY_copy["Adj Close"] - 62.919998)/62.919998

# Use a new ref_Close price ($110.879997), Feb 04, 2021 (after the GME craziness)
SONY_copy["a_ref_Close"] = SONY_copy["Adj Close"] - 110.879997
# New % change from the new reference day: Feb 04, 2021
SONY_copy["a_Perc_ref"] = (SONY_copy["Adj Close"] - 110.879997)/110.879997

print(SONY_copy.shape)
SONY_copy.head()

(462, 11)


Date       Open       High        Low      Close  Adj Close   Volume  \
0  2020-01-02  68.300003  69.059998  68.279999  69.059998  69.059998   856500   
1  2020-01-03  68.500000  68.650002  67.959999  68.080002  68.080002   518600   
2  2020-01-06  68.250000  69.199997  68.220001  69.110001  69.110001   755500   
3  2020-01-07  70.510002  70.580002  69.809998  70.199997  70.199997  1316200   
4  2020-01-08  70.800003  71.120003  70.370003  70.459999  70.459999  1640200   

   b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref  
0     6.140000    0.097584   -41.819999   -0.377165  
1     5.160004    0.082009   -42.799995   -0.386003  
2     6.190003    0.098379   -41.769996   -0.376714  
3     7.279999    0.115702   -40.680000   -0.366883  
4     7.540001    0.119835   -40.419998   -0.364538

In [24]:
# # Import and prepare NASDAQ (^IXIC) fund index
# file_path12 = Path("Resources/IXIC.csv")
# IXIC_df = pd.read_csv(file_path12)
# print(IXIC_df.shape)
# IXIC_df.head(5)

In [25]:
# # Shift the reference point to the start date, Jan 1, 2020
# IXIC_copy = IXIC_df.copy()

# # Subtract the "Adj Close" price on Apr 28, 2020 price from future stocks.
# # This is reference "zero"
# IXIC_copy["b_ref_Close"] = IXIC_copy["Adj Close"] - 8607.730469
# # Calculate the % change from the reference day
# IXIC_copy["b_Perc_ref"] = (IXIC_copy["Adj Close"] - 8607.730469)/8607.730469

# # Use a new ref_Close price ($13777.740234), Feb 04, 2021 (after the GME craziness)
# IXIC_copy["a_ref_Close"] = IXIC_copy["Adj Close"] - 13777.740234
# # New % change from the new reference day: Feb 04, 2021
# IXIC_copy["a_Perc_ref"] = (IXIC_copy["Adj Close"] - 13777.740234)/13777.740234

# print(IXIC_copy.shape)
# IXIC_copy.head()

### Combine all the stocks

In [26]:
# Isert a "Ticker" column
GME_copy["Ticker"] = "GME"
AMC_copy["Ticker"] = "AMC"
BBBY_copy["Ticker"] = "BBBY"
VOO_copy["Ticker"] = "VOO"
BNTX_copy["Ticker"] = "BNTX"
AXP_copy["Ticker"] = "AXP"
MSFT_copy["Ticker"] = "MSFT"
DIS_copy["Ticker"] = "DIS"
MARA_copy["Ticker"] = "MARA"
EA_copy["Ticker"] = "EA"
SONY_copy["Ticker"] = "SONY"
# IXIC_copy["Ticker"] = "NASDAQ"


# Combine all the stocks in a single dataframe
stocks = [GME_copy, AMC_copy, BBBY_copy, VOO_copy, BNTX_copy, AXP_copy,
         MSFT_copy, DIS_copy, MARA_copy, EA_copy, SONY_copy]
combined_all_df = pd.concat(stocks)

# Reindex the dataframe
combined_all_df.reset_index(drop=True, inplace=True)

print(combined_all_df.shape)
combined_all_df.sample(5)

(5081, 12)


Date        Open        High         Low       Close   Adj Close  \
2992  2020-11-16  214.869995  217.740005  214.520004  217.229996  214.861740   
4587  2021-09-16  137.910004  139.699997  135.529999  135.960007  135.960007   
4249  2020-05-14  116.500000  117.260002  114.459999  117.120003  116.541924   
3878  2020-09-23    1.810000    1.850000    1.640000    1.640000    1.640000   
3600  2021-06-17  174.589996  176.259995  173.839996  174.649994  174.649994   

        Volume  b_ref_Close  b_Perc_ref  a_ref_Close  a_Perc_ref Ticker  
2992  24953300    47.773407    0.285917   -25.136520   -0.104736   MSFT  
4587   4637600    25.159607    0.227071    -2.169555   -0.015707     EA  
4249   2802800     5.741524    0.051819   -21.587638   -0.156285     EA  
3878   4071000     1.200000    2.727273   -21.159999   -0.928070   MARA  
3600   8906000    68.439995    0.644384    -5.580002   -0.030960    DIS

In [27]:
# Drop the "Close" column since it is almost a duplicate of the Adj Close
combined_all = combined_all_df.drop(columns="Close")
combined_all['Net_Close'] = combined_all['Adj Close'] - combined_all['Open']
combined_all['Net_High'] = combined_all['High'] - combined_all['Open']
combined_all.head()

Date  Open  High   Low  Adj Close   Volume  b_ref_Close  b_Perc_ref  \
0  2020-01-02  6.14  6.47  6.07       6.31  4453600         0.67    0.118794   
1  2020-01-03  6.21  6.25  5.84       5.88  3543900         0.24    0.042553   
2  2020-01-06  5.80  5.91  5.60       5.85  3394800         0.21    0.037234   
3  2020-01-07  5.77  5.83  5.44       5.52  5228000        -0.12   -0.021277   
4  2020-01-08  5.49  5.85  5.41       5.72  5629400         0.08    0.014184   

   a_ref_Close  a_Perc_ref Ticker  Net_Close  Net_High  
0       -47.19   -0.882056    GME       0.17      0.33  
1       -47.62   -0.890093    GME      -0.33      0.04  
2       -47.65   -0.890654    GME       0.05      0.11  
3       -47.98   -0.896822    GME      -0.25      0.06  
4       -47.78   -0.893084    GME       0.23      0.36

In [28]:
# Check the datatypes
combined_all.dtypes

Date            object
Open           float64
High           float64
Low            float64
Adj Close      float64
Volume           int64
b_ref_Close    float64
b_Perc_ref     float64
a_ref_Close    float64
a_Perc_ref     float64
Ticker          object
Net_Close      float64
Net_High       float64
dtype: object

In [29]:
combined_all.Date = pd.to_datetime(combined_all.Date)

In [30]:
# Make a line plot to see the data 
combined_all.hvplot(x='Date', y='b_ref_Close', by='Ticker', 
                     label='Change in the stock closing price compared to the Adj closing price on Apr 28, 2020', 
                    ylabel='Change in closing price', width=800, height=400)

:NdOverlay   [Ticker]
   :Curve   [Date]   (b_ref_Close)

In [31]:
combined_all.hvplot(x='Date', y='a_ref_Close', by='Ticker', 
                     label='Change in the stock closing price compared to the Adj closing price on Feb 4, 2021', 
                    ylabel='Change in closing price', width=800, height=400)

:NdOverlay   [Ticker]
   :Curve   [Date]   (a_ref_Close)

In [32]:
# Make a line plot to see the how the stocks changed from the reference date, April 28, 2020
combined_all.hvplot(x='Date', y='b_Perc_ref', by='Ticker', 
                     label='%Change in the stock closing price compared to the Adj closing price on Apr 28, 2020', 
                    ylabel='% Change in closing price', width = 800, height=450)

:NdOverlay   [Ticker]
   :Curve   [Date]   (b_Perc_ref)

In [33]:
# Make a line plot to see the how the stocks changed from the reference date, Feb 4 2021
combined_all.hvplot(x='Date', y='a_Perc_ref', by='Ticker', 
                     label='%Change in the stock closing price compared to the Adj closing price on Apr 28, 2020', 
                    ylabel='% Change in closing price', width = 800, height=450)

:NdOverlay   [Ticker]
   :Curve   [Date]   (a_Perc_ref)

In [34]:
# Plot the heatmap to see how different stocks changed over one year.
combined_all.hvplot.heatmap(x="Date", y="Ticker", C="b_ref_Close", hover_cols="High",
                            colorbar=True, width=800, rot=45, 
                            label = "Heatmap showing 11 stocks intraday High price variation from 01/01/2020 until 10/31/2021")

:HeatMap   [Date,Ticker]   (b_ref_Close,High)

#### Plot the percent change each day

In [35]:
# Plot the heatmap to see how different stocks changed over one year.
combined_all.hvplot.heatmap(x="Date", y="Ticker", C="b_Perc_ref", hover_cols="High",
                            colorbar=True, width=800, rot=45, 
                            label = "Heatmap showing % change from the referance intra day price variation")

:HeatMap   [Date,Ticker]   (b_Perc_ref,High)

In [36]:
# Plot the heatmap to see how different stocks changed over Jan 1 until March 30, 2021
# From Stackoverflow: Create a mask that is greater than the start date and smaller than 
# the end date.
mask = (combined_all["Date"] > '2021-01-01') & (combined_all["Date"] <= '2021-03-20')
x_mask = combined_all.loc[mask]

x_mask.hvplot.heatmap(x='Date', y='Ticker', C="b_Perc_ref", hover_cols='High', width = 800,
                     label="Heatmap showing the change in price from 01-01-2020 between Jan 01 - March 30, 2021")

:HeatMap   [Date,Ticker]   (b_Perc_ref,High)

### Plot stock trend after the GME explosion. Feb 04, 2021 seems like a good place to start. Note, the stock 'Adj Close' price on Feb 04, 2021 is reference "zero".

In [37]:
mask1 = (combined_all["Date"] > '2021-02-03') & (combined_all["Date"] <= '2021-10-29')
x_mask1 = combined_all.loc[mask1]

# Plot the % change from the reference date without NASDAQ
x_mask1.hvplot(x="Date", y="a_Perc_ref", by="Ticker", hover_cols='High', width=800, height=450,
                ylabel="% change of the stock price", 
                label="% change of the stock price from the reference date, Feb 04 2021")

:NdOverlay   [Ticker]
   :Curve   [Date]   (a_Perc_ref,High)

In [38]:
mask2 = (combined_all["Date"] > '2021-02-03') & (combined_all["Date"] <= '2021-10-29')
x_mask2 = combined_all.loc[mask2]

# Plot the % change from the reference date without NASDAQ
x_mask2.hvplot(x="Date", y="a_Perc_ref", by="Ticker", hover_cols='High', width=800, height=450,
                ylabel="% change of the stock price", 
                label="% change of the stock price from the reference date, Feb 04 2021")

:NdOverlay   [Ticker]
   :Curve   [Date]   (a_Perc_ref,High)

In [39]:
### Write a CSV file of the combined stocks for Machine Learning
combined_all.to_csv("Resources/stocks_11_bf_af.csv")